Informatics 2 - Foundations of Data Science

# Hypothesis testing

David Sterratt, 2020-2024

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import binom
import pandas as pd
import seaborn as sns
from scipy.stats import expon
from scipy.stats import norm
from scipy.stats import chi2
from scipy import stats
import pandas as pd
import matplotlib
matplotlib.rcParams['figure.dpi'] = 300

## Swain vs. Alabama

In [ ]:
population_proportions = [.26, .74]
population_proportions

In [ ]:
# Example of np.random.choice
# np.random.choice(['Black', 'Non-black'], 100, True, population_proportions)

In [ ]:
def panel_number_black():
    panel = np.random.choice(['Black', 'Non-black'], 100, True, population_proportions)
    return(np.sum(panel == 'Black'))

panel_number_black()

### Statistical simulation

In [ ]:
k = 10000
panels = np.zeros(k)

for i in np.arange(k):
    panels[i] = panel_number_black()

In [ ]:
plt.figure(figsize=(6, 2))
plt.subplot(1, 2, 1)
hist_panels = plt.hist(panels, bins=np.arange(5.5,40.), density=True)
plt.vlines( 8, 0, 0.02, color='red')
plt.vlines(15, 0, 0.02, color='magenta')
plt.vlines(20, 0, 0.02, color='yellow')


plt.title('Simulation')

plt.xlabel('Number of Black people on panel')
plt.ylabel('Relative frequency')

plt.subplot(1, 2, 2)

n = 100
p = population_proportions[0]
x = np.arange(0, 40, 1)

plt.plot(x, binom.pmf(x, n, p), 'o', ms=4, label='binom pmf')
plt.plot(x, norm.pdf(x, n*p, np.sqrt(n*p*(1-p))))

ax = plt.gca()
ax.vlines(x, 0, binom.pmf(x, n, p), alpha=0.5)

#plt.scatter(8, 0.005, color='red')
plt.vlines( 8, 0, 0.02, color='red')
plt.vlines(15, 0, 0.02, color='magenta')
plt.vlines(20, 0, 0.02, color='yellow')


plt.title('Binomial distribution')
plt.ylabel('Probability')
plt.xlabel('Number of Black people on panel')
plt.tight_layout()
plt.savefig('swain-versus-alabama.pdf')
plt.savefig('swain-versus-alabama.png')

### p-values from simulation

Firstly, with original data $t_0=8$:

In [ ]:
pvalue_8 = np.sum(hist_panels[0][np.where(hist_panels[1] < 8)])
pvalue_8

Then with artificial data $t_0=20$:

In [ ]:
pvalue_20 = np.sum(hist_panels[0][np.where(hist_panels[1] < 20)])
pvalue_20

Finally with artificial data $t_0=15$.

In [ ]:
pvalue_15 = np.sum(hist_panels[0][np.where(hist_panels[1] < 15)])
pvalue_15

In [ ]:
hist_panels[0]

In [ ]:
hist_panels[1]

In [ ]:
np.min(panels)

### p-values from Z-test

Since $n$ is large we can use the normal approximation: $\mu=np$ and $\sigma =\sqrt{np(1-p)}$. We then compute $z = \frac{t_0-\mu}{\sigma}$, and find _p_-value from the cumulative distribution of the normal function (aka "Standard normal curve areas" in statistical tables).

In [ ]:
n = 100
p = population_proportions[0]
mu = n*p
sigma = np.sqrt(n*p*(1-p))
z = (8 - mu)/sigma
norm.cdf(z)

In [ ]:
z = (20 - mu)/sigma
norm.cdf(z)

In [ ]:
t_0 = [8, 15, 20]
p_values = pd.DataFrame({'t_0': t_0,
                         'Simulation': [pvalue_8, pvalue_15, pvalue_20],
                        'Binomial': binom.cdf(t_0, n=n, p=p),
                         'Normal': norm.cdf(t_0, loc=n*p, scale=np.sqrt(n*p*(1-p)))})

# p_values.to_latex('swain-p-values.tex', float_format='%3.3g')
p_values

## Rejection regions

In [ ]:
mu = n*p
sigma = np.sqrt(n*p*(1-p))
x = np.arange(0, 40, 0.1)

plt.figure(figsize=(6,2.5))

## One tailed
plt.subplot(1,2,1)
plt.plot(x, norm.pdf(x, mu, sigma), color='blue')

# x_lower = np.linspace(0, mu + sigma*norm.isf(1-0.1))
# plt.fill_between(x_lower, x_lower*0, norm.pdf(x_lower, mu, sigma), color='brown', label='p<0.1')
# x_lower = np.linspace(0, mu + sigma*norm.isf(1-0.05))
# plt.fill_between(x_lower, x_lower*0, norm.pdf(x_lower, mu, sigma), color='orange', label='p<0.05')
# x_lower = np.linspace(0, mu + sigma*norm.isf(1-0.01))
# plt.fill_between(x_lower, x_lower*0, norm.pdf(x_lower, mu, sigma), color='yellow', label='p<0.01')

x_lower = mu + sigma*norm.isf(1-0.1)
plt.vlines(x_lower, 0, norm.pdf(x_lower, mu, sigma), color='brown', label='p<0.1')
x_lower = mu + sigma*norm.isf(1-0.05)
plt.vlines(x_lower, 0, norm.pdf(x_lower, mu, sigma), color='orange', label='p<0.05')
x_lower = mu + sigma*norm.isf(1-0.01)
plt.vlines(x_lower, 0, norm.pdf(x_lower, mu, sigma), color='lightblue', label='p<0.01')

plt.scatter(15, 0, color='magenta')
plt.xlabel('$T_0$')
plt.title('Lower-tailed')
plt.legend()

# Two tailed
plt.subplot(1,2,2)

plt.plot(x, norm.pdf(x, mu, sigma), color='blue')

# x_lower = np.linspace(0, mu + sigma*norm.isf(1-0.05))
# plt.fill_between(x_lower, x_lower*0, norm.pdf(x_lower, mu, sigma), color='brown', label='p<0.1')
# x_upper = np.linspace(40, mu + sigma*norm.isf(0.05))
# plt.fill_between(x_upper, x_upper*0, norm.pdf(x_upper, mu, sigma), color='brown')

x_lower = mu + sigma*norm.isf(1-0.05)
plt.vlines(x_lower, 0, norm.pdf(x_lower, mu, sigma), color='brown', label='p<0.1')
x_upper = mu + sigma*norm.isf(0.05)
plt.vlines(x_upper, 0, norm.pdf(x_upper, mu, sigma), color='brown')

# x_lower = np.linspace(0, mu + sigma*norm.isf(1-0.025))
# plt.fill_between(x_lower, x_lower*0, norm.pdf(x_lower, mu, sigma), color='orange', label='p<0.05')
# x_upper = np.linspace(40, mu + sigma*norm.isf(0.025))
# plt.fill_between(x_upper, x_upper*0, norm.pdf(x_upper, mu, sigma), color='orange')

x_lower = mu + sigma*norm.isf(1-0.025)
plt.vlines(x_lower, 0, norm.pdf(x_lower, mu, sigma), color='orange', label='p<0.05')
x_upper = mu + sigma*norm.isf(0.025)
plt.vlines(x_upper, 0, norm.pdf(x_upper, mu, sigma), color='orange')

# x_lower = np.linspace(0, mu + sigma*norm.isf(1-0.005))
# plt.fill_between(x_lower, x_lower*0, norm.pdf(x_lower, mu, sigma), color='yellow', label='p<0.01')
# x_upper = np.linspace(40, mu + sigma*norm.isf(0.005))
# plt.fill_between(x_upper, x_upper*0, norm.pdf(x_upper, mu, sigma), color='yellow')

x_lower = mu + sigma*norm.isf(1-0.005)
plt.vlines(x_lower, 0, norm.pdf(x_lower, mu, sigma), color='lightblue', label='p<0.01')
x_upper = mu + sigma*norm.isf(0.005)
plt.vlines(x_upper, 0, norm.pdf(x_upper, mu, sigma), color='lightblue')


plt.scatter(15, 0, color='magenta')
plt.xlabel('$T_0$')
plt.title('Two-tailed')
plt.legend()

plt.tight_layout()
plt.savefig('rejection-regions.png')
plt.savefig('rejection-regions.pdf')


## Multiple categories - Alameda county

### Data

In [ ]:
dat = pd.DataFrame({'Population %': {'Caucasian': 54, 'Black/AA': 18, 'Hispanic': 12,
                                             'Asian/PI': 15, 'Other': 1},
                   'Observed panel numbers': {'Caucasian': 780, 'Black/AA': 117, 'Hispanic': 114,
                                             'Asian/PI': 384, 'Other': 58}})
dat = dat.transpose()
# dat['Total'] = dat.sum~(1)

dat.loc['Expected panel numbers'] = dat.loc['Population %']/100*dat.loc['Observed panel numbers'].sum()
dat.loc['(Observed-Expected)^2/Expected'] = \
    np.power(dat.loc['Expected panel numbers'] - dat.loc['Observed panel numbers'], 2) / \
    dat.loc['Expected panel numbers']

dat['Total'] = dat.sum(1)

# dat.to_latex('alameda-cell-counts.tex', float_format='%2.2f')

### Statistical simulation of $\chi^2$ statistic

In [ ]:
K = 1000 # Number of repetitions
n_obs = dat.drop('Total', axis=1).loc['Observed panel numbers']
p = dat.drop('Total', axis=1).loc['Population %']/100
k = len(p) # Number of categories
n = np.sum(n_obs)
n_exp = n*p
chi2 = np.zeros(K)

for j in range(K):
    # Sample
    n_sim = np.random.multinomial(n, p)
    chi2[j] = np.sum(np.power((n_sim - n_exp), 2)/n_exp)

Plot the distribution from the simulation, along with the theoretical distribution ($\chi^2$ with $k-1$ degrees of freedom).

In [ ]:
plt.figure(figsize=(4, 3))
plt.hist(chi2, 50, density=True, label='Simulation')
x = np.arange(0, 30)
plt.plot(x, stats.chi2.pdf(x, k-1), label='Prob. distribution')
plt.legend()
plt.xlabel('$\chi^2$')
plt.tight_layout()
plt.savefig('alameda-chi2-dist.pdf')
plt.savefig('alameda-chi2-dist.png')

In [ ]:
# stats.chi2.pdf(x, 2)
# stats.chi2.pdf(x, k-1)

## Homogeneity

In [ ]:
n_obs = pd.DataFrame({'Female': {'Depressed': round(2078*1.44/100), 'Not depressed': round(2078*(100-1.44)/100)},
                   'Male': {'Depressed': round(1675*0.7/100), 'Not depressed': round(1675*(100-0.7)/100)}})


In [ ]:
n_obs_tot = n_obs.copy()
n_obs_tot['Total'] = n_obs.sum(1)
n_obs_tot.loc['Total'] = n_obs_tot.sum(0)
p_Depressed = n_obs_tot.loc['Depressed', 'Total']/n_obs_tot.loc['Total', 'Total']

In [ ]:
# p_Depressed = np.mean(n_obs_tot.loc['Depressed', ['Female', 'Male']]/n_obs_tot.loc['Total', ['Female', 'Male']])


In [ ]:
p_Depressed

In [ ]:
n_exp = pd.DataFrame({'Depressed': p_Depressed * n_obs_tot.loc['Total', ['Female', 'Male']],
                     'Not depressed': (1 - p_Depressed) * n_obs_tot.loc['Total', ['Female', 'Male']]}).transpose()

In [ ]:
# n_exp.to_latex('contingency-table-exp.tex', float_format='%2.2f')

In [ ]:
chisq = np.sum(np.sum(np.power(n_exp - n_obs, 2)/n_exp))

In [ ]:
chisq

In [ ]:
1 - stats.chi2.cdf(chisq, df=1)

In [ ]:
1 - stats.chi2.cdf(chisq, 2)

In [ ]:
chisq*0.79

In [ ]:
ni = n_obs.sum(1)
nj = n_obs.sum(0)
n = ni.sum()

In [ ]:
n_exp = np.array([ni]).transpose() * np.array(nj)/n